In [1]:
import src.Utils as Utils
from src.CovidClassifier import CovidClassifier
from src.CoughDetector import CoughDetector
import librosa
import pandas as pd
import numpy as np
import datetime
import librosa
import matplotlib.pyplot as plt
import seaborn as sns
import os
import pathlib
import dask.dataframe as dd
from dask.multiprocessing import get
import numpy as np
import librosa
from scipy import signal
from scipy.io import wavfile
from scipy.signal import butter,filtfilt
from scipy.stats import kurtosis
import scipy.signal as signal
from scipy.integrate import simps

import numpy as np
import pandas as pd
 



In [2]:
SYMPTOMS = [
    'fever',
    'dry cough',
    'tiredness',
    'difficulty breathing or shortness of breath',
    'chest pain or pressure',
    'loss of speech or movement',
    'aches and pains',
    'sore throat',
    'diarrhoea',
    'conjunctivitis',
    'headache',
    'loss of taste or smell',
    'a rash on skin, or discolouration of fingers or toes'
]




In [3]:
# Classifiers
COUGH_DETECTOR = CoughDetector()


In [4]:
COVID_CLASSIFIER = CovidClassifier()

In [5]:
# def detect_cough(x,path = '/home/abrol/ARYAN_MT22019/CoughVid/public_dataset/'):
    
#     try:
#          recording, sr = librosa.load(os.path.join(path, x+".webm"))
         
#     except:
#          return "error"
#     features = COUGH_DETECTOR.extract_features(recording, sr)
#     return features

In [6]:
def load_wave(x,path = '/home/abrol/ARYAN_MT22019/CoughVid/public_dataset/'):
    
    try:
         recording, sr = librosa.load(os.path.join(path, x+".webm"))
         return recording
         
    except:
         return "error"
    

In [7]:
# x,fs= librosa.load('/home/abrol/ARYAN_MT22019/CoughVid/public_dataset/fffce9f0-a5e8-4bee-b13b-c671aac4a61c.webm')


In [8]:
# detect_cough(x = "fffce9f0-a5e8-4bee-b13b-c671aac4a61c").shape

In [9]:
df = pd.read_csv('/home/abrol/ARYAN_MT22019/CoughVid/public_dataset/metadata_compiled.csv')

In [10]:
df.head()


uuid                          datetime  \
0  00039425-7f3a-42aa-ac13-834aaa2b6b92  2020-04-13T21:30:59.801831+00:00   
1  0009eb28-d8be-4dc1-92bb-907e53bc5c7a  2020-04-12T04:02:18.159383+00:00   
2  0012c608-33d0-4ef7-bde3-75a0b1a0024e  2020-04-15T01:03:59.029326+00:00   
3  001328dc-ea5d-4847-9ccf-c5aa2a3f2d0f  2020-04-13T22:23:06.997578+00:00   
4  001c85a8-cc4d-4921-9297-848be52d4715  2020-04-17T15:24:35.822355+00:00   

   cough_detected  latitude  longitude   age gender respiratory_condition  \
0          0.9609      31.3       34.8  15.0   male                 False   
1          0.9301      40.0      -75.1  34.0   male                  True   
2          0.0482     -16.5      -71.5   NaN    NaN                   NaN   
3          0.9968       NaN        NaN  21.0   male                 False   
4          0.0735      40.6       -3.6   NaN    NaN                   NaN   

  fever_muscle_pain   status  ... quality_3 dyspnea_3 wheezing_3 stridor_3  \
0             False  healthy  ...       NaN       NaN        NaN       NaN   
1             False  healthy  ...       NaN       NaN        NaN       NaN   
2               NaN      NaN  ...       NaN       NaN        NaN       NaN   
3             False  healthy  ...       NaN       NaN        NaN       NaN   
4               NaN      NaN  ...       NaN       NaN        NaN       NaN   

  choking_3 congestion_3 nothing_3 cough_type_3 diagnosis_3 severity_3  
0       NaN          NaN       NaN          NaN         NaN        NaN  
1       NaN          NaN       NaN          NaN         NaN        NaN  
2       NaN          NaN       NaN          NaN         NaN        NaN  
3       NaN          NaN       NaN          NaN         NaN        NaN  
4       NaN          NaN       NaN          NaN         NaN        NaN  

[5 rows x 40 columns]

In [36]:
df['date'] = pd.to_datetime(df['datetime'])
df['year'] = df['date'].dt.year
df['month'] = df['date'].dt.month
df['day'] = df['date'].dt.day
df['day_of_week'] = df['date'].dt.day_of_week
df['day_of_year'] = df['date'].dt.day_of_year

def get_time_interval(hour):
    if 5 <= hour < 12:
        return 'Morning'
    elif 12 <= hour < 16:
        return 'Afternoon'
    elif 16<= hour <20:
        return 'Evening'
    else: 
        return 'Night'

df['TimeOfDay'] = df['date'].dt.hour.apply(get_time_interval)

def categorize_age(age):
    if age < 18:
        return 'Children'
    elif 18 <= age < 60:
        return 'Adults'
    else:
        return 'Seniors'

# Create a new column "AgeGroup" based on the age categories
df['AgeGroup'] = df['age'].apply(categorize_age)

def season(date, latitude):
    ''' date is a datetime object
        hemisphere is either 'north' or 'south', dependent on long/lat.
    '''
    if latitude<=0:
        hemisphere = 'south'
    else: 
        hemisphere = 'north'
    md = date.month * 100 + date.day

    if ((md > 320) and (md < 621)):
        s = 0 #spring
    elif ((md > 620) and (md < 923)):
        s = 1 #summer
    elif ((md > 922) and (md < 1223)):
        s = 2 #fall
    else:
        s = 3 #winter

    if hemisphere != 'north':
        if s < 2:
            s += 2 
        else:
            s -= 2

    return s

df["Season"] = -1
for i in range(len(df)):
    df['Season'][i]  = season(df['date'][i], df['latitude'][i])

df["Season"].replace({0:"Spring",
                      1:"Summer",
                      2:"Fall",
                      3:"winter"}, inplace=True )   



/tmp/ipykernel_2699845/1920567301.py:60: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Season'][i]  = season(df['date'][i], df['latitude'][i])


In [12]:
ddf = dd.from_pandas(df['uuid'], npartitions=8192) 

In [13]:
ddf_audio = ddf.apply(load_wave).compute()

/tmp/ipykernel_2699845/1732247012.py:4: UserWarning: PySoundFile failed. Trying audioread instead.
  recording, sr = librosa.load(os.path.join(path, x+".webm"))
/home/abrol/miniconda3/envs/Cough/lib/python3.11/site-packages/librosa/core/audio.py:183: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/home/abrol/miniconda3/envs/Cough/lib/python3.11/site-packages/dask/dataframe/core.py:4419: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('uuid', 'object'))

  warnings.warn(meta_warning(meta))
/tmp/ipykernel_26

In [14]:
ddf_audio.head()

0    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
Name: uuid, dtype: object

In [15]:
ddf_audio.rename('wave', inplace=True)

0        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4        [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
                               ...                        
20067    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
20068    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
20069    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
20070    [-2.4104492e-09, -1.8044831e-09, -1.0693204e-0...
20071    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
Name: wave, Length: 20072, dtype: object

In [23]:
ddf_audio.to_numpy()

array([array([0., 0., 0., ..., 0., 0., 0.], dtype=float32),
       array([ 0.        ,  0.        ,  0.        , ..., -0.00023587,
              -0.00053528, -0.00125644], dtype=float32)               ,
       array([0., 0., 0., ..., 0., 0., 0.], dtype=float32), ...,
       array([0., 0., 0., ..., 0., 0., 0.], dtype=float32),
       array([-2.4104492e-09, -1.8044831e-09, -1.0693204e-09, ...,
              -6.8631363e-03, -7.2680162e-03, -9.9394210e-03], dtype=float32),
       array([ 0.        ,  0.        ,  0.        , ..., -0.00231448,
              -0.00201326, -0.0017971 ], dtype=float32)               ],
      dtype=object)

In [37]:
result = pd.concat([df, ddf_audio], axis=1)
result['uuid'] #.head()
result.head()

uuid                          datetime  \
0  00039425-7f3a-42aa-ac13-834aaa2b6b92  2020-04-13T21:30:59.801831+00:00   
1  0009eb28-d8be-4dc1-92bb-907e53bc5c7a  2020-04-12T04:02:18.159383+00:00   
2  0012c608-33d0-4ef7-bde3-75a0b1a0024e  2020-04-15T01:03:59.029326+00:00   
3  001328dc-ea5d-4847-9ccf-c5aa2a3f2d0f  2020-04-13T22:23:06.997578+00:00   
4  001c85a8-cc4d-4921-9297-848be52d4715  2020-04-17T15:24:35.822355+00:00   

   cough_detected  latitude  longitude   age gender respiratory_condition  \
0          0.9609      31.3       34.8  15.0   male                 False   
1          0.9301      40.0      -75.1  34.0   male                  True   
2          0.0482     -16.5      -71.5   NaN    NaN                   NaN   
3          0.9968       NaN        NaN  21.0   male                 False   
4          0.0735      40.6       -3.6   NaN    NaN                   NaN   

  fever_muscle_pain   status  ... date_issued:day_of_year  TimeOfDay  \
0             False  healthy  ...                     104      Night   
1             False  healthy  ...                     103      Night   
2               NaN      NaN  ...                     106      Night   
3             False  healthy  ...                     104      Night   
4               NaN      NaN  ...                     108  Afternoon   

   AgeGroup  Season  year month day day_of_week day_of_year  \
0  Children  Spring  2020     4  13           0         104   
1    Adults  Spring  2020     4  12           6         103   
2   Seniors    Fall  2020     4  15           2         106   
3    Adults  Spring  2020     4  13           0         104   
4   Seniors  Spring  2020     4  17           4         108   

                                                wave  
0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
2  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  

[5 rows x 55 columns]

In [38]:
pwd

'/home/abrol/ARYAN_MT22019/CoughVid'

In [40]:
# result.to_csv('features_covid.csv', index = False)


In [33]:
# daskdf = dd.from_pandas(result['uuid'], npartitions=4096) 

In [34]:
# daskdf_audio_features = dasdf.apply(detect_cough).compute()

In [41]:
result.head()

uuid                          datetime  \
0  00039425-7f3a-42aa-ac13-834aaa2b6b92  2020-04-13T21:30:59.801831+00:00   
1  0009eb28-d8be-4dc1-92bb-907e53bc5c7a  2020-04-12T04:02:18.159383+00:00   
2  0012c608-33d0-4ef7-bde3-75a0b1a0024e  2020-04-15T01:03:59.029326+00:00   
3  001328dc-ea5d-4847-9ccf-c5aa2a3f2d0f  2020-04-13T22:23:06.997578+00:00   
4  001c85a8-cc4d-4921-9297-848be52d4715  2020-04-17T15:24:35.822355+00:00   

   cough_detected  latitude  longitude   age gender respiratory_condition  \
0          0.9609      31.3       34.8  15.0   male                 False   
1          0.9301      40.0      -75.1  34.0   male                  True   
2          0.0482     -16.5      -71.5   NaN    NaN                   NaN   
3          0.9968       NaN        NaN  21.0   male                 False   
4          0.0735      40.6       -3.6   NaN    NaN                   NaN   

  fever_muscle_pain   status  ... date_issued:day_of_year  TimeOfDay  \
0             False  healthy  ...                     104      Night   
1             False  healthy  ...                     103      Night   
2               NaN      NaN  ...                     106      Night   
3             False  healthy  ...                     104      Night   
4               NaN      NaN  ...                     108  Afternoon   

   AgeGroup  Season  year month day day_of_week day_of_year  \
0  Children  Spring  2020     4  13           0         104   
1    Adults  Spring  2020     4  12           6         103   
2   Seniors    Fall  2020     4  15           2         106   
3    Adults  Spring  2020     4  13           0         104   
4   Seniors  Spring  2020     4  17           4         108   

                                                wave  
0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
2  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  

[5 rows x 55 columns]

In [54]:
import logging
from math import pi
from scipy.fftpack import fft, hilbert

In [55]:
def get_period(signal, signal_sr):
        """Extract the period from the the provided signal
        :param signal: the signal to extract the period from
        :type signal: numpy.ndarray
        :param signal_sr: the sampling rate of the input signal
        :type signal_sr: integer
        :return: a vector containing the signal period
        :rtype: numpy.ndarray
        """

        # perform a sanity check
        if signal is None:
            raise ValueError("Input signal cannot be None")

        # transform the signal to the hilbert space
        hy = hilbert(signal)

        ey = np.sqrt(signal ** 2 + hy ** 2)
        min_time = 1.0 / signal_sr
        tot_time = len(ey) * min_time
        pow_ft = np.abs(fft(ey))
        peak_freq = pow_ft[3: int(len(pow_ft) / 2)]
        peak_freq_pos = peak_freq.argmax()
        peak_freq_val = 2 * pi * (peak_freq_pos + 2) / tot_time
        period = 2 * pi / peak_freq_val

        return np.array([period])

In [88]:

def extract_audio_features(signal, fs):
        """Extract part of handcrafted features from the input signal.
        :param signal: the signal the extract features from
        :type signal: numpy.ndarray
        :param signal_sr: the sample rate of the signal
        :type signal_sr: integer
        :return: the populated feature vector
        :rtype: numpy.ndarray
        """
        try:
          frame_len = int(fs / 10)  # 100 ms
          hop = int(frame_len / 2)  # 50% overlap, meaning 5ms hop length

          # normalise the sound signal before processing
          signal = signal / np.max(np.abs(signal))
          

          # trim the signal to the appropriate length
          trimmed_signal, idc = librosa.effects.trim(signal, frame_length=frame_len, hop_length=hop)

          # extract the signal duration
          signal_duration = librosa.get_duration(y=trimmed_signal, sr=fs)
         


          # find the onset strength of the trimmed signal
          o_env = librosa.onset.onset_strength(s=trimmed_signal, sr=fs)
          print("hi")

          # find the frames of the onset
          onset_frames = librosa.onset.onset_detect(onset_envelope=o_env, sr=fs)
          

          # keep only the first onset frame
          onsets = onset_frames.shape[0]

          # decompose the signal into its magnitude and the phase components such that signal = mag * phase
          mag, phase = librosa.magphase(librosa.stft(trimmed_signal, n_fft=frame_len, hop_length=hop))

          # extract the rms from the magnitude component
          rms = librosa.feature.rms(y=trimmed_signal)[0]
          s = pd.Series(rms)
          rms_skew = s.skew()

          # extract the spectral bandwith of the magnitude
          spec_bandwidth = librosa.feature.spectral_bandwidth(S=mag)[0]

          
          # pack the extracted features into the feature vector to be returned
          signal_features = np.concatenate(
              (
                  np.array([signal_duration, onsets]),
                  get_period(signal, signal_sr=fs),
                  np.array([np.max(rms), np.median(rms), np.percentile(rms, 25), rms_skew]),
                      np.array([np.mean(spec_bandwidth)])
              ),
              axis=0,
          )
          return signal_features

        except:
            logging.error('Error extracting audio features.')
            return np.zeros(8)



In [89]:
x,fs= librosa.load('/home/abrol/ARYAN_MT22019/CoughVid/public_dataset/fffce9f0-a5e8-4bee-b13b-c671aac4a61c.webm')

/tmp/ipykernel_2699845/617801714.py:1: UserWarning: PySoundFile failed. Trying audioread instead.
  x,fs= librosa.load('/home/abrol/ARYAN_MT22019/CoughVid/public_dataset/fffce9f0-a5e8-4bee-b13b-c671aac4a61c.webm')
/home/abrol/miniconda3/envs/Cough/lib/python3.11/site-packages/librosa/core/audio.py:183: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


In [90]:
extract_audio_features(signal=x, fs=fs)

ERROR:root:Error extracting audio features.


array([0., 0., 0., 0., 0., 0., 0., 0.])

array([0., 0., 0., ..., 0., 0., 0.], dtype=float32)